In [ ]:
cd Desktop/

In [ ]:
cd data_gen/

In [ ]:
import pandas as pd
df = pd.read_parquet("hf://datasets/Raja4321123/Gemini-2.0-flash-scenario-dataset/data/train-00000-of-00001.parquet")

/usr/local/lib/python3.10/dist-packages/huggingface_hub/utils/_auth.py:94: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


In [ ]:
df

In [ ]:
df["old_incorrect_web_ret"]

In [ ]:
!pip install langchain
!pip install torch
!pip install transformers
!pip install sentence-transformers
!pip install datasets
!pip install faiss-gpu

In [ ]:
pip install faiss-gpu

In [ ]:
!pip install -U langchain-community

In [ ]:
from langchain.document_loaders import HuggingFaceDatasetLoader
from langchain.text_splitter import RecursiveCharacterTextSplitter
from langchain.embeddings import HuggingFaceEmbeddings
from langchain.vectorstores import FAISS

In [ ]:
pip install datasets


In [ ]:
import pandas as pd

In [ ]:
df = pd.read_csv("llama_3_final - final.csv.csv")

In [ ]:
df

In [ ]:
df = df.head(100)

In [ ]:
from datasets import Dataset, DatasetDict


# Convert DataFrame to Dataset
dataset = Dataset.from_pandas(df)

# Create a DatasetDict
dataset_dict = DatasetDict({"train": dataset})


In [ ]:
dataset_dict

DatasetDict({
    train: Dataset({
        features: ['section', 'title', 'abstract', 'url', 'human_story_fetched', 'web_retrieved_urls', 'old_incorrect_web_ret', 'new_correct_web_ret', 'wrong_web_content_ranked', 'wrong_human_story_fetched', 'ai_generated_article_with_context_(human_story_fetched)', 'ai_generated_article_without_context', 'ai_generated_article_with_context_(web_content_ranked)', 'ai_generated_article_with_context_(wrong_human_story_fetched)'],
        num_rows: 939
    })
})

In [ ]:
page_content_column = "old_incorrect_web_ret"  # Replace with the column you're interested in

data = dataset_dict["train"][page_content_column]
print(data)

['The new report is a sign that inflation is cooling again after proving sticky early in 2024, and it could help to inform Fed officials as they set out a future path for interest rates.\nSource: Bureau of Labor Statistics By Karl Russell Subscribe to The Times to read as many articles as you like.\nThe latest news for any part of the world you select.\nThe latest data could help to restore their conviction that inflation is in the process of returning to the central bank’s goal.\n+ 10 % Inflation + 8 + 6 +3.4% excluding food and energy + 4 +3.3% in May + 2 0 – 2 ’05 ’10 ’15 ’20 + 14 % + 12 Inflation + 10 + 8 +3.4% excluding food and energy + 6 + 4 +3.3% in May + 2 0 – 2 1965 ’70 ’75 ’80 ’85 ’90 ’95 2000 ’05 ’10 ’15 ’20 + 14 % + 12 Inflation + 10 + 8 + 6 +3.4% excluding food and energy + 4 +3.3% in May + 2 0 – 2 1965 ’70 ’75 ’80 ’85 ’90 ’95 2000 ’05 ’10 ’15 ’20 Year-over-year change in the Consumer Price Index Source: Bureau of Labor Statistics By Karl Russell By Jeanna Smialek Just ho

In [ ]:
type(data)

list

In [ ]:
data[:1]

In [ ]:
import torch

In [ ]:
# Create an instance of the RecursiveCharacterTextSplitter class with specific parameters.
# It splits text into chunks of 1000 characters each with a 150-character overlap.
text_splitter = RecursiveCharacterTextSplitter(chunk_size=500, chunk_overlap=100)

# Convert the list of strings in 'data' to a list of Document objects, filtering out None values
from langchain.schema import Document
docs_ = [Document(page_content=text) for text in data if text is not None]

# 'docs_' now holds a list of Document objects, split the text into documents using the text splitter.
docs = text_splitter.split_documents(docs_)

In [ ]:
print(torch.cuda.is_available())

True


In [ ]:
# Define the path to the pre-trained model you want to use
modelPath = "WhereIsAI/UAE-Large-V1"

# Create a dictionary with model configuration options, specifying to use the CPU for computations
model_kwargs = {'device':'cuda'}

# Create a dictionary with encoding options, specifically setting 'normalize_embeddings' to False
encode_kwargs = {'normalize_embeddings': False}

# Initialize an instance of HuggingFaceEmbeddings with the specified parameters
embeddings = HuggingFaceEmbeddings(
    model_name=modelPath,     # Provide the pre-trained model's path
    model_kwargs=model_kwargs, # Pass the model configuration options
    encode_kwargs=encode_kwargs # Pass the encoding options
)

In [ ]:
db = FAISS.from_documents(docs, embeddings)
db.save_local(folder_path="db/faiss_db", index_name="myFaissIndex")

In [ ]:
db.save_local(folder_path="db/faiss_db", index_name="myFaissIndex")

In [ ]:
from tqdm.notebook import tqdm

In [ ]:
db = FAISS.load_local(folder_path="db/faiss_db",
                     embeddings=embeddings,
                     index_name="myFaissIndex",
                     allow_dangerous_deserialization=True # Add this line
                    )
searchDocs = db.similarity_search("Inflation slowed, good news as the Fed meets.", k =7)
print(searchDocs[0].page_content)

The minutes of the Fed’s June 11-12 meeting, released Wednesday, showed that the policymakers saw several factors that could further ease inflation in the coming months.
We can also afford to consider the labor market.' " Though Fed officials generally see the economy as healthy, the minutes showed greater concern about signs of a slowdown.
Powell said the Fed had made “quite a bit of progress” toward bringing inflation back to 2%.
Rate cuts by the Fed would likely lead, over time, to lower borrowing costs for mortgages, auto loans and credit cards as well as business borrowing, and could also boost stock prices.
Got a confidential news tip?
However, in the Fed parlance, “a number” is considered more than “several.” The summary also noted a “vast majority” saw economic growth “gradually cooling” and that the current policy is “restrictive,” a key term as the officials contemplate how restrictive policy needs to be while bringing down inflation and not causing undue economic harm.


In [ ]:
len(searchDocs)

7

In [ ]:
df

In [ ]:
searchDocs = db.similarity_search("Inflation slowed, good news as the Fed meets.")
print(searchDocs[1].page_content)

In [ ]:
from tqdm.notebook import tqdm

# Define a function to perform the similarity search and return the top 3 results
def get_top_7_search_results(query, db):
    searchDocs = db.similarity_search(query, k =8)
    # Extract the page_content of the top 3 results
    top_7_contents = [doc.page_content for doc in searchDocs[:6]]
    # Combine the results into a single string (you can customize how you combine them)
    return " | ".join(top_7_contents)

# Initialize the progress bar
tqdm.pandas(desc="Processing Titles")

# Apply the function to each row in the DataFrame, using the 'title' as the query, with a progress bar
df['rag_context'] = df['abstract'].progress_apply(lambda abstract: get_top_7_search_results(abstract, db))

# Display the DataFrame to see the new column
print(df[['abstract', 'rag_context']])


Processing Titles:   0%|          | 0/939 [00:00<?, ?it/s]

In [ ]:
df.to_csv( "fia.csv", index = False)
